In [36]:
# Module was created referencing '18-Unsupervised-Learning-Day2-Solved'


# Initial imports
import pandas as pd
import hvplot.pandas
import plotly.express as px
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans
import matplotlib.pyplot as plt

from datetime import datetime

# Clean up CMO-Monthly-prices

In [37]:
#Pull
indices_df = pd.read_csv(r'Resources/Data/CMO-Monthly-Indices.csv', index_col = 0)
indices_df.index.name = 'Month'
indices_df.head()

#Select only the data for 2016-2021
years = ("2016|2017|2018|2019|2020|2021")
indices_df = indices_df[indices_df.index.str.contains(years)]
indices_df.to_csv('clean_indices.csv')

# Clean up Contracts csv

In [38]:
awards_df = pd.read_csv(r'Resources/Data/Contracts_PrimeAwardSummaries_2016-2022_NAICS_21.csv', index_col = 0)
awards_df

# Count Null Values
#for column in awards_df.columns:
    #print(f"Column {column} has {awards_df[column].isnull().sum()} null values")

#Select only data for 2016-2021
years = ("2016|2017|2018|2019|2020|2021")
awards_df = awards_df[awards_df.award_base_action_date.str.contains(years)]
awards_df

award_base_action_date  \
total_obligated_amount                          
10000.00                            9/26/2016   
1384.98                             2/18/2016   
542491.46                           5/12/2017   
21764.63                             3/4/2016   
256800.00                           12/5/2020   
...                                       ...   
451.80                              9/19/2018   
99950.00                            5/28/2021   
29982.00                            8/10/2021   
138.21                              12/8/2016   
751.70                               1/4/2018   

                       period_of_performance_start_date  \
total_obligated_amount                                    
10000.00                                      9/26/2016   
1384.98                                       2/18/2016   
542491.46                                     5/12/2017   
21764.63                                       3/4/2016   
256800.00                                     12/5/2020   
...                                                 ...   
451.80                                        9/21/2018   
99950.00                                      5/28/2021   
29982.00                                      8/10/2021   
138.21                                        12/8/2016   
751.70                                         1/4/2018   

                       period_of_performance_current_end_date  \
total_obligated_amount                                          
10000.00                                      10/31/2016 0:00   
1384.98                                         4/5/2016 0:00   
542491.46                                      7/11/2017 0:00   
21764.63                                       3/17/2016 0:00   
256800.00                                     12/27/2020 0:00   
...                                                       ...   
451.80                                         9/25/2018 0:00   
99950.00                                       9/30/2021 0:00   
29982.00                                        8/9/2022 0:00   
138.21                                        12/28/2016 0:00   
751.70                                          1/9/2018 0:00   

                       period_of_performance_potential_end_date  \
total_obligated_amount                                            
10000.00                                        10/31/2016 0:00   
1384.98                                           4/5/2016 0:00   
542491.46                                        8/10/2017 0:00   
21764.63                                         3/17/2016 0:00   
256800.00                                       12/27/2020 0:00   
...                                                         ...   
451.80                                           9/25/2018 0:00   
99950.00                                         9/30/2021 0:00   
29982.00                                          8/9/2022 0:00   
138.21                                          12/28/2016 0:00   
751.70                                            1/9/2018 0:00   

                               funding_sub_agency_name  \
total_obligated_amount                                   
10000.00                              DEPT OF THE NAVY   
1384.98                          FEDERAL PRISON SYSTEM   
542491.46                     DEFENSE LOGISTICS AGENCY   
21764.63                          STATE, DEPARTMENT OF   
256800.00                             DEPT OF THE ARMY   
...                                                ...   
451.80                                DEPT OF THE ARMY   
99950.00                                FOREST SERVICE   
29982.00                U.S. FISH AND WILDLIFE SERVICE   
138.21                        DEFENSE LOGISTICS AGENCY   
751.70                        DEFENSE LOGISTICS AGENCY   

                                                  recipient_name  \
total_obligated_amount                                             
10000.00

In [39]:
#Convert the date columns to datetime format to match indices_df
columns = ['award_base_action_date']
awards_df.award_base_action_date = pd.to_datetime(awards_df.award_base_action_date)

awards_df.award_base_action_date = awards_df.award_base_action_date.dt.strftime('%YM%m')


# Create new df with only necessary columns
clean_contracts_df = awards_df[['award_base_action_date','product_or_service_code_description', 'naics_description', 'funding_sub_agency_name']]

clean_contracts_df

award_base_action_date  \
total_obligated_amount                          
10000.00                              2016M09   
1384.98                               2016M02   
542491.46                             2017M05   
21764.63                              2016M03   
256800.00                             2020M12   
...                                       ...   
451.80                                2018M09   
99950.00                              2021M05   
29982.00                              2021M08   
138.21                                2016M12   
751.70                                2018M01   

                          product_or_service_code_description  \
total_obligated_amount                                          
10000.00                      GASES: COMPRESSED AND LIQUEFIED   
1384.98                  MINERAL CONSTRUCTION MATERIALS, BULK   
542491.46               MAINTENANCE OF FUEL SUPPLY FACILITIES   
21764.63                 OTHER QC/TEST/INSPECT- MISCELLANEOUS   
256800.00                MINERAL CONSTRUCTION MATERIALS, BULK   
...                                                       ...   
451.80                   MINERAL CONSTRUCTION MATERIALS, BULK   
99950.00                 MINERAL CONSTRUCTION MATERIALS, BULK   
29982.00                 MINERAL CONSTRUCTION MATERIALS, BULK   
138.21                          NAILS, MACHINE KEYS, AND PINS   
751.70                                BEVERAGES, NONALCOHOLIC   

                                                        naics_description  \
total_obligated_amount                                                      
10000.00                                    NATURAL GAS LIQUID EXTRACTION   
1384.98                               CONSTRUCTION SAND AND GRAVEL MINING   
542491.46                   SUPPORT ACTIVITIES FOR OIL AND GAS OPERATIONS   
21764.63                              CONSTRUCTION SAND AND GRAVEL MINING   
256800.00               OTHER CRUSHED AND BROKEN STONE MINING AND QUAR...   
...                                                                   ...   
451.80                  OTHER CRUSHED AND BROKEN STONE MINING AND QUAR...   
99950.00                              CONSTRUCTION SAND AND GRAVEL MINING   
29982.00                                            PHOSPHATE ROCK MINING   
138.21                                 SUPPORT ACTIVITIES FOR COAL MINING   
751.70                            POTASH, SODA, AND BORATE MINERAL MINING   

                               funding_sub_agency_name  
total_obligated_amount                                  
10000.00                              DEPT OF THE NAVY  
1384.98                          FEDERAL PRISON SYSTEM  
542491.46                     DEFENSE LOGISTICS AGENCY  
21764.63                          STATE, DEPARTMENT OF  
256800.00                             DEPT OF THE ARMY  
...                                                ...  
451.80                                DEPT OF THE ARMY  
99950.00                                FOREST SERVICE  
29982.00                U.S. FISH AND WILDLIFE SERVICE  
138.21                        DEFENSE LOGISTICS AGENCY  
751.70                        DEFENSE LOGISTICS AGENCY  

[10580 rows x 4 columns]

In [40]:
# Group together total spending by NAICS
clean_contracts_df = clean_contracts_df.groupby(['naics_description','product_or_service_code_description', 'award_base_action_date','total_obligated_amount']).sum()
clean_contracts_df.to_csv('clean_contracts.csv')

# Clean up CMO prices

In [41]:
#Pull
prices_df = pd.read_csv(r'Resources/Data/CMO-Monthly-Prices.csv', index_col = 0)
prices_df.index.name = 'Month'
prices_df.head()

#Select only the data for 2016-2021
years = ("2016|2017|2018|2019|2020|2021")
prices_df = prices_df[prices_df.index.str.contains(years)]
prices_df.to_csv('clean_prices.csv')

In [42]:
prices_df

Crude oil, average  Crude oil, Brent  Crude oil, Dubai  \
Month                                                             
2016M01               29.78             30.80             27.00   
2016M02               31.03             33.20             29.50   
2016M03               37.34             39.07             35.18   
2016M04               40.75             42.25             39.04   
2016M05               45.94             47.13             43.95   
...                     ...               ...               ...   
2021M08               68.87             70.02             68.85   
2021M09               72.80             74.60             72.24   
2021M10               82.06             83.65             81.22   
2021M11               79.92             80.77             79.80   
2021M12               72.87             74.31             72.76   

        Crude oil, WTI Coal, Australian Coal, South African **  \
Month                                                            
2016M01          31.54            49.02                  49.09   
2016M02          30.39            50.27                  50.33   
2016M03          37.77            52.21                  52.57   
2016M04          40.96            50.69                  52.35   
2016M05          46.73            51.31                  54.24   
...                ...              ...                    ...   
2021M08          67.73           169.58                 137.92   
2021M09          71.56           185.69                 146.05   
2021M10          81.32           224.51                 199.65   
2021M11          79.18           157.48                    128   
2021M12          71.53           169.65                  142.5   

         Natural gas, US  Natural gas, Europe ** Liquefied natural gas, Japan  \
Month                                                                           
2016M01             2.27                    4.40                          8.4   
2016M02             1.96                    3.97                         8.56   
2016M03             1.70                    3.91                         7.74   
2016M04             1.90                    3.97                         6.82   
2016M05             1.92                    4.33                         6.27   
...                  ...                     ...                          ...   
2021M08             4.05                   15.43                         10.8   
2021M09             5.11                   22.84                        11.44   
2021M10             5.48                   31.05                        12.38   
2021M11             5.02                   27.62                        15.25   
2021M12             3.73                   38.03                        15.32   

        Natural gas index  ...  Aluminum  Iron ore, cfr spot   Copper  \
Month                      ...                                          
2016M01             54.22  ...   1481.10               41.88  4471.79   
2016M02             48.43  ...   1531.26               46.83  4598.62   
2016M03             44.49  ...   1531.01               56.20  4953.80   
2016M04             46.63  ...   1571.23               60.92  4872.74   
2016M05             48.17  ...   1550.63               55.13  4694.54   
...                   ...  ...       ...                 ...      ...   
2021M08            129.82  ...   2602.99              162.16  9370.14   
2021M09             178.4  ...   2834.56              124.52  9324.71   
2021M10            222.53  ...   2934.39              122.91  9829.22   
2021M11            202.59  ...   2636.45               96.24  9728.90   
2021M12            236.49  ...   2695.53              116.96  9551.18   

            Lead       Tin    Nickel     Zinc     Gold Platinum Silver  
Month                                                                   
2016M01  1646.20  13808.08   8507.29  1520.36  1097.91   855.25  14.11  
2016M02  1765.75  15610.14   8298.50  1709.85  1199.50 

# US Natural Gas Production

In [55]:
import json

with open(r'Resources/Data/nat_gas_production.json','r') as f:
    data = json.loads(f.read())

gas_prod_df = pd.json_normalize(data, record_path=['response'])
gas_prod_df

TypeError: {'response': {'query execution': 0.731134366, 'count query execution': 0.740400375, 'total': 19400, 'dateFormat': 'YYYY', 'frequency': 'annual', 'data': [{'period': 1977, 'duoarea': 'R19F', 'area-name': 'NA', 'product': 'EPG0', 'product-name': 'Natural Gas', 'process': 'FGW', 'process-name': 'Gross Withdrawals', 'series': 'NA1060_R19F_2', 'series-description': 'Federal Offshore--Louisiana Natural Gas Gross Withdrawals (MMcf)'}, {'period': 1983, 'duoarea': 'R19F', 'area-name': 'NA', 'product': 'EPG0', 'product-name': 'Natural Gas', 'process': 'FGW', 'process-name': 'Gross Withdrawals', 'series': 'NA1060_R19F_2', 'series-description': 'Federal Offshore--Louisiana Natural Gas Gross Withdrawals (MMcf)'}, {'period': 1986, 'duoarea': 'R19F', 'area-name': 'NA', 'product': 'EPG0', 'product-name': 'Natural Gas', 'process': 'FGW', 'process-name': 'Gross Withdrawals', 'series': 'NA1060_R19F_2', 'series-description': 'Federal Offshore--Louisiana Natural Gas Gross Withdrawals (MMcf)'}, {